## Enable the geo-visualization for the dataset

In [14]:
pip install folium

Note: you may need to restart the kernel to use updated packages.


In [76]:
import pandas as pd
import folium

# Load TSV data
haunted_df = pd.read_csv('../Data/haunted_places_with_alcohol_daylight.tsv', sep='\t')

# Initialize the map
m = folium.Map(
    location=[37.8, -96.9],  # Approximate U.S. center
    zoom_start=4,
    tiles='CartoDB Positron'  # Clean basemap
)

# Add simple markers
for idx, row in haunted_df.iterrows():
    folium.CircleMarker(
        location=[row['latitude'], row['longitude']],
        radius=2,  # Tiny dot
        color='red',
        fill=True,
        fill_color='red'
    ).add_to(m)


In [78]:
m

## Add the geometry for haunted houses data
The coordinate system of the dataset is WGS84 which is indiced with 4326

In [160]:
from shapely.geometry import Point

haunted_gdf = gpd.GeoDataFrame(
    haunted_df,
    geometry=[Point(xy) for xy in zip(haunted_df.longitude, haunted_df.latitude)],
    crs=4326
)

## Add the 1st dataset
This dataset is a combined with two datasets. This first one is the GeoJSON file representing the shapes of all counties in the United States. The second dataset is a census data includes the population(2020), the number of religious adherents (who have a religious faith), and the percentage of that proportion for each county, in .xlsx format. 

### Prepare the combined dataset

In [162]:
import pandas as pd
import geopandas as gpd

# Load Counties GeoJSON
counties_gdf = gpd.read_file('../Data/georef-united-states-of-america-county.geojson')

counties_gdf = counties_gdf.rename(columns={
    'ste_name': 'state',
    'coty_name': 'county'
})
# I'm doing this step because those fields are String List type instead of String type
counties_gdf['state'] = counties_gdf['state'].apply(lambda x: ' '.join(x) if isinstance(x, list) else str(x))
counties_gdf['county'] = counties_gdf['county'].apply(lambda x: ' '.join(x) if isinstance(x, list) else str(x))

counties_gdf['state'] = counties_gdf['state'].str.strip().str.title()
counties_gdf['county'] = counties_gdf['county'].str.strip().str.title()

# Load Census Data
census_df = pd.read_excel(
    '../Data/2020_USRC_Summaries.xlsx', 
    sheet_name='2020 County Summary'  # Specify the sheet name
)

census_df = census_df.rename(columns={
    'State Name': 'state',
    'County Name': 'county'
})

census_df['county'] = census_df['county'].str.replace(' County', '', regex=False)

census_df['state'] = census_df['state'].str.strip().str.title()
census_df['county'] = census_df['county'].str.strip().str.title()

# Merge County geometries with Census data
counties_merged = counties_gdf.merge(
    census_df,
    on=['state', 'county'],
    how='left'
)

### Join the combined dataset to the haunted houses dataset

In [164]:
# Spatial Join with Counties
joined_df = haunted_gdf.sjoin(
    counties_merged[['geometry', 'county', '2020 Population', 'Adherents', 'Adherents as % of Population']],
    how='left',
    predicate='within'
)

### Calculate and add the field "count of haunted houses per county"

In [166]:
county_counts = joined_df.groupby('county').size().reset_index(name='Haunted Houses Count per County')

# Merge counts back into the main dataset
joined_df = pd.merge(
    joined_df,
    county_counts,
    on='county',
    how='left'
)

### Calculate and add the field "count of haunted houses per 1000 people in the county"

In [168]:
joined_df['Haunted houses per 1000'] = (joined_df['Haunted Houses Count per County'] / joined_df['2020 Population']) * 1000

In [188]:
joined_df

city        country  \
0                Ada  United States   
1            Addison  United States   
2             Adrian  United States   
3             Adrian  United States   
4             Albion  United States   
...              ...            ...   
10969    Westminster  United States   
10970    Westminster  United States   
10971    Wheat Ridge  United States   
10972    Wheat Ridge  United States   
10973  Woodland Park  United States   

                                             description  \
0      Ada witch - Sometimes you can see a misty blue...   
1      A little girl was killed suddenly while waitin...   
2      If you take Gorman Rd. west towards Sand Creek...   
3      In the 1970's, one room, room 211, in the old ...   
4      Kappa Delta Sorority - The Kappa Delta Sororit...   
...                                                  ...   
10969  at 12 midnight you can see a lady with two lit...   
10970  Is haunted by the victims of a murder that hap...   
10971  The institution was for kids 18 years old and ...   
10972  Gymnasium -  their have been reports of a litt...   
10973  Cadets from the Air Force Academy participatin...   

                        location     state state_abbrev   longitude  \
0                   Ada Cemetery  Michigan           MI  -85.504893   
1                North Adams Rd.  Michigan           MI  -84.381843   
2                  Ghost Trestle  Michigan           MI  -84.035656   
3       Siena Heights University  Michigan           MI  -84.017565   
4                 Albion College  Michigan           MI  -84.745177   
...                          ...       ...          ...         ...   
10969                  city hall  Colorado           CO -105.048936   
10970             Pillar of Fire  Colorado           CO -105.032091   
10971   Ridge Mental Institution  Colorado           CO -105.063974   
10972  Wheat Ridge Middle School  Colorado           CO -105.103613   
10973         Saylor Park Forest  Colorado           CO -105.022763   

        latitude  city_longitude  city_latitude  ...  \
0      42.962106      -85.495480      42.960727  ...   
1      41.971425      -84.347168      41.986434  ...   
2      41.904538      -84.037166      41.897547  ...   
3      41.905712      -84.037166      41.897547  ...   
4      42.244006      -84.753030      42.243097  ...   
...          ...             ...            ...  ...   
10969  39.862610     -105.037205      39.836653  ...   
10970  39.847237     -105.037205      39.836653  ...   
10971  39.769726     -105.077206      39.766098  ...   
10972  39.764055     -105.077206      39.766098  ...   
10973  39.116658     -105.056930      38.993881  ...   

       find sunrise and sunset for other places….3  \
0                                              NaN   
1                                              NaN   
2                                              NaN   
3                                              NaN   
4                                              NaN   
...                                            ...   
10969                                          NaN   
10970                                          NaN   
10971                                          NaN   
10972                                          NaN   
10973                                          NaN   

       find sunrise and sunset for other places….4  \
0                                              NaN   
1                                              NaN   
2                                              NaN   
3                                              NaN   
4                                              NaN   
...                                            ...   
10969                                          NaN   
10970                                          NaN   
10971                                          NaN   
10972                                          NaN   
10973                                          NaN   

  